In [1]:
import torch
import time
import pandas as pd
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.nn.utils import rnn
from ast import literal_eval
from sklearn.metrics import f1_score
from sklearn.metrics import classification_report
from gensim.models import KeyedVectors
from gensim.models.keyedvectors import Word2VecKeyedVectors
from sklearn.model_selection import train_test_split

In [2]:
df = pd.read_csv("data/reviews_preprocessed.csv")

In [16]:
df.head()

Unnamed: 0                                              title  \
0           0          ['Ідеально', 'для', 'ділової', 'поїздки']   
1           1  ['Затишний', 'чистий', 'номер', 'з', 'усіма', ...   
2           2               ['Все', 'сподобалося', 'Рекомендую']   
3           3  ['Зручне', 'розташування', 'чудовий', 'вигляд'...   
4           4                  ['Все', 'чудово', '9,9', 'балів']   

                                                 pos  \
0  ['Ідеально', 'для', 'ділової', 'поїздки', 'Гос...   
1  ['Затишний', 'чистий', 'номер', 'з', 'усіма', ...   
2  ['Чисто', 'тихо', 'комфортно', 'Зустрів', 'і',...   
3  ['Зручне', 'розташування', 'чудовий', 'вигляд'...   
4  ['Нові', 'апартаменти', 'на', 'останньому', 'п...   

                                                 neg  ratingValue  bestRating  \
0                                            ['Nan']         10.0        10.0   
1  ['При', 'бронюванні', 'вказала', 'час', 'прибу...          9.2        10.0   
2  ['На', 'барі', 'кава', 'тільки', '3', 'в', '1'...          9.6        10.0   
3                                            ['Nan']         10.0        10.0   
4  ['Немає', 'терміналу', 'для', 'оплати', 'креди...         10.0        10.0   

   rate  
0     1  
1     1  
2     1  
3     1  
4     1

In [4]:
embeddings_file = "./embeddings/ubercorpus.cased.tokenized.word2vec.300d"

In [5]:
word2vec = KeyedVectors.load_word2vec_format(embeddings_file)

In [ ]:
# def create_word2idx_and_embeddings(word2vec):
#     word_embeddings = np.zeros((len(word2vec.vocab), word2vec.vector_size + 3))
#     word2idx = {}
#     for word in word2vec.vocab:
#         idx = len(word2idx)
#         word2idx[word] = idx
#         word_embeddings[idx] = np.append(word2vec[word], [0, 0, 0])

#     word_embeddings = torch.tensor(word_embeddings, dtype=torch.float32)
#     return word2idx, word_embeddings

In [6]:
def create_word2idx_and_embeddings(word2vec):
    word_embeddings = np.zeros((len(word2vec.vocab), word2vec.vector_size))
    word2idx = {}
    for word in word2vec.vocab:
        idx = len(word2idx)
        word2idx[word] = idx
        word_embeddings[idx] = word2vec[word]

    word_embeddings = torch.tensor(word_embeddings, dtype=torch.float32)
    return word2idx, word_embeddings

In [7]:
word2idx, word_embeddings = create_word2idx_and_embeddings(word2vec)

In [8]:
def get_features_and_target(data):
    X = []
    y = []
    
    for i in range(0, len(data)):
        title = literal_eval(data.iloc[i]['title'])
        if  len(title) > 0 and title[0] == 'Nan':
            title = []
            
        pos = literal_eval(data.iloc[i]['pos'])
        if len(pos) > 0 and pos[0] == 'Nan':
            pos = []


        neg = literal_eval(data.iloc[i]['neg'])
        if len(neg) > 0 and neg[0] == 'Nan':
            neg = []


        
        x = title + pos + neg
        if len(x) == 0:
            continue
            
        X.append(x)
        
        y.append(data.iloc[i]['rate'] + 1)
        
    return X, y

In [9]:
X, y = get_features_and_target(df)

In [10]:
len(X)

15985

In [11]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42)

In [20]:
class LSTMClassifier(nn.Module):
    """
    Args:
        embedding_dim -- 300
        hidden_dim -- hidden state dimensionality
        vocab_size -- vocabulary size
        num_classes -- number of classes
        pretrained_embeddings -- None or [vocab_size, embedding_dim] tensor
    """
    def __init__(self, embedding_dim, hidden_dim, vocab_size, num_classes,
                 num_layers=2,
                 pretrained_embeddings=None, device='cpu'):

        super(LSTMClassifier, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_classes = num_classes
        self.num_layers = num_layers
        self.word_embeddings = nn.Embedding(vocab_size, embedding_dim)
        if pretrained_embeddings is not None:
            self.word_embeddings = nn.Embedding.from_pretrained(pretrained_embeddings,
                                                                freeze=True).to(device)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim,
                            num_layers=self.num_layers,
                            bidirectional=False, batch_first=True)
        self.cls = nn.Linear(hidden_dim*self.num_layers, self.num_classes)
        self.dropout = nn.Dropout(p=0.4)
        self.device = device
        self.to(self.device)

    def forward(self, inputs):
        embeds = rnn.PackedSequence(self.word_embeddings(inputs.data), inputs.batch_sizes)
        h0 = torch.randn(self.num_layers, inputs.batch_sizes[0], self.hidden_dim).to(self.device)
        c0 = torch.randn(self.num_layers, inputs.batch_sizes[0], self.hidden_dim).to(self.device)
        lstm_out, (hidden, cell) = self.lstm(embeds, (h0, c0))
        hidden = hidden.permute(1,0,2).contiguous().view(inputs.batch_sizes[0], -1)
        scores = F.log_softmax(self.cls(self.dropout(hidden)), dim=1)
        return scores

In [21]:
class Trainer:
    def __init__(self, model, loss_fn, optimizer, word_to_idx, device='cpu'):
        self.model = model
        self.loss_fn = loss_fn
        self.optimizer = optimizer
        self.word_to_idx = word_to_idx
        self.device = device
        
    
    def fit(self, num_epochs, 
            X_train, y_train, train_batch_size, 
            X_val, y_val, val_batch_size, 
            log_interval=50):
        for epoch in range(1, num_epochs+1):
            self.__train(epoch, X_train, y_train, train_batch_size, log_interval)
            self.__validate(epoch, X_val, y_val, val_batch_size)
            
            
    def __train(self, epoch, X, y, batch_size, log_interval=5):
        batch_start = 0
        batch_idx = 0
        while batch_start < len(X):
            start = time.time()
            
            self.optimizer.zero_grad()

            X_batch = X[batch_start:batch_start + batch_size]
            y_batch = y[batch_start:batch_start + batch_size]
            
            inputs_packed, targets_batch = self.__create_batch(X_batch, y_batch)
            inputs_packed = inputs_packed.to(self.device)
            targets_batch = targets_batch.to(self.device)
            outputs = self.model(inputs_packed)

            loss = self.loss_fn(outputs, targets_batch)
            loss.backward()
            self.optimizer.step()
            
            exec_time = time.time() - start

            batch_start += batch_size
            batch_idx += 1
            
            if batch_idx % log_interval == 0:
                print(f"Train Epoch: {epoch} {min(batch_start, len(X))}/{len(X)}. Loss: {loss.item()}. Time: {exec_time} s")        
                
    def __validate(self, epoch, X, y, batch_size):
        with torch.no_grad():
            batch_start = 0
            batch_idx = 0
            start = time.time()
            while batch_start < len(X):
                

                X_batch = X[batch_start:batch_start + batch_size]
                y_batch = y[batch_start:batch_start + batch_size]

                inputs_packed, targets_batch = self.__create_batch(X_batch, y_batch)
                
                inputs_packed = inputs_packed.to(self.device)
                targets_batch = targets_batch.to(self.device)
                outputs = self.model(inputs_packed)
                
                loss = self.loss_fn(outputs, targets_batch)
                F1 = self.__calc_F1_score_avg(outputs, targets_batch)

                batch_start += batch_size
                batch_idx += 1
        
        exec_time = time.time() - start
        print(f"=====> Validation. Epoch: {epoch}. Loss: {loss.item()}, F-1 score: {F1}. Time: {exec_time} s")
        
    
    def test(self, X_test, y_test, target_names):
        with torch.no_grad():
            inputs_packed, targets_batch = self.__create_batch(X_test, y_test)
            inputs_packed = inputs_packed.to(self.device)
            targets_batch = targets_batch.to(self.device)
            outputs = self.model(inputs_packed)
            
            y_pred = outputs.max(dim=1)[1]
            
        return classification_report(targets_batch, y_pred, target_names=target_names)
        
                
    
    def __seq_to_idxs(self, seq, mapping):    
        outs_seq = []
        for el in seq:
            if el in mapping:
                outs_seq.append(torch.tensor(mapping[el], dtype=torch.long))
        outs_seq = torch.stack(outs_seq, 0)
        return outs_seq
    
    def __create_batch(self, x_batch, y_batch):
        inputs_batch = [self.__seq_to_idxs(seq, word2idx) for seq in x_batch]

        order = sorted(enumerate(inputs_batch), key=lambda x: len(x[1]), reverse=True)
        inputs_batch = [inputs_batch[order_[0]] for order_ in order]
        targets_batch = torch.tensor([y_batch[order_[0]] for order_ in order])


        inputs_packed = rnn.pack_sequence(inputs_batch)

        return inputs_packed, targets_batch
    
    def __calc_F1_score_avg(self, outputs, targets):
        pred = outputs.max(dim=1)[1]
        F1 = f1_score(pred, targets, average='weighted')
        return F1


In [22]:
hidden_dim = 128
learning_rate = 0.01

vocab_size = len(word2idx)
num_classes = 3
device = 'cpu' if not torch.cuda.is_available() else 'cuda'

model = LSTMClassifier(embedding_dim=word_embeddings.shape[1],
                       hidden_dim=hidden_dim,
                       vocab_size=vocab_size,
                       num_classes=num_classes,
                       pretrained_embeddings=word_embeddings,
                       device=device)
loss_function = nn.NLLLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate)

train_batch_size = 32
val_batch_size = 32

trainer = Trainer(model, loss_function, optimizer, word2idx, device=device)
trainer.fit(512, X_train, y_train, train_batch_size, X_val, y_val, val_batch_size, 1)

Train Epoch: 1 32/10230. Loss: 1.0871572494506836. Time: 0.21463704109191895 s
Train Epoch: 1 64/10230. Loss: 1.0563734769821167. Time: 0.4117250442504883 s
Train Epoch: 1 96/10230. Loss: 0.9236616492271423. Time: 0.47272300720214844 s
Train Epoch: 1 128/10230. Loss: 1.0143420696258545. Time: 0.12136197090148926 s
Train Epoch: 1 160/10230. Loss: 1.0506302118301392. Time: 0.33156490325927734 s
Train Epoch: 1 192/10230. Loss: 0.8388464450836182. Time: 0.12883687019348145 s
Train Epoch: 1 224/10230. Loss: 0.9522609710693359. Time: 0.24785900115966797 s
Train Epoch: 1 256/10230. Loss: 0.953240692615509. Time: 0.10763406753540039 s
Train Epoch: 1 288/10230. Loss: 0.8464271426200867. Time: 0.15323281288146973 s
Train Epoch: 1 320/10230. Loss: 0.9479492902755737. Time: 0.19916892051696777 s
Train Epoch: 1 352/10230. Loss: 1.2493788003921509. Time: 0.19678592681884766 s
Train Epoch: 1 384/10230. Loss: 0.9063747525215149. Time: 0.15744376182556152 s
Train Epoch: 1 416/10230. Loss: 1.00360310077

Train Epoch: 1 3360/10230. Loss: 0.7313739061355591. Time: 0.13112688064575195 s
Train Epoch: 1 3392/10230. Loss: 0.9125488996505737. Time: 0.16801214218139648 s
Train Epoch: 1 3424/10230. Loss: 0.9638820886611938. Time: 0.2090129852294922 s
Train Epoch: 1 3456/10230. Loss: 0.6652806997299194. Time: 0.15377306938171387 s
Train Epoch: 1 3488/10230. Loss: 0.8109328746795654. Time: 0.16115403175354004 s
Train Epoch: 1 3520/10230. Loss: 0.780341386795044. Time: 0.2197880744934082 s
Train Epoch: 1 3552/10230. Loss: 0.6257141828536987. Time: 0.19255614280700684 s
Train Epoch: 1 3584/10230. Loss: 0.683617353439331. Time: 0.15285611152648926 s
Train Epoch: 1 3616/10230. Loss: 1.2152185440063477. Time: 0.26427698135375977 s
Train Epoch: 1 3648/10230. Loss: 0.755853533744812. Time: 0.17131280899047852 s
Train Epoch: 1 3680/10230. Loss: 0.8788887858390808. Time: 0.15973305702209473 s
Train Epoch: 1 3712/10230. Loss: 0.9193133115768433. Time: 0.13363003730773926 s
Train Epoch: 1 3744/10230. Loss: 

Train Epoch: 1 6656/10230. Loss: 1.0682494640350342. Time: 0.33646202087402344 s
Train Epoch: 1 6688/10230. Loss: 0.5554595589637756. Time: 0.2228541374206543 s
Train Epoch: 1 6720/10230. Loss: 0.7020052075386047. Time: 0.17722797393798828 s
Train Epoch: 1 6752/10230. Loss: 0.7371445298194885. Time: 0.19124293327331543 s
Train Epoch: 1 6784/10230. Loss: 0.9302141666412354. Time: 0.15811681747436523 s
Train Epoch: 1 6816/10230. Loss: 0.8090776801109314. Time: 0.2694120407104492 s
Train Epoch: 1 6848/10230. Loss: 0.791368842124939. Time: 0.14999103546142578 s
Train Epoch: 1 6880/10230. Loss: 0.6306213140487671. Time: 0.34828996658325195 s
Train Epoch: 1 6912/10230. Loss: 0.8876264095306396. Time: 0.3215451240539551 s
Train Epoch: 1 6944/10230. Loss: 0.7011825442314148. Time: 0.19450712203979492 s
Train Epoch: 1 6976/10230. Loss: 0.8483805656433105. Time: 0.36046600341796875 s
Train Epoch: 1 7008/10230. Loss: 0.8492931127548218. Time: 0.40296292304992676 s
Train Epoch: 1 7040/10230. Loss:

Train Epoch: 1 9952/10230. Loss: 0.8122982978820801. Time: 0.23147010803222656 s
Train Epoch: 1 9984/10230. Loss: 0.7470090389251709. Time: 0.24060702323913574 s
Train Epoch: 1 10016/10230. Loss: 0.7911249995231628. Time: 0.24103808403015137 s
Train Epoch: 1 10048/10230. Loss: 0.7006933689117432. Time: 0.27527403831481934 s
Train Epoch: 1 10080/10230. Loss: 0.8283948302268982. Time: 0.3161308765411377 s
Train Epoch: 1 10112/10230. Loss: 0.7813900113105774. Time: 0.14562416076660156 s
Train Epoch: 1 10144/10230. Loss: 0.8695300221443176. Time: 0.2195451259613037 s
Train Epoch: 1 10176/10230. Loss: 0.7394719123840332. Time: 0.14870667457580566 s
Train Epoch: 1 10208/10230. Loss: 0.9030547142028809. Time: 0.1712181568145752 s
Train Epoch: 1 10230/10230. Loss: 0.8495028018951416. Time: 0.13906598091125488 s
=====> Validation. Epoch: 1. Loss: 0.9087013602256775, F-1 score: 0.5777777777777777. Time: 4.0804078578948975 s
Train Epoch: 2 32/10230. Loss: 0.8645339608192444. Time: 0.2078971862792

Train Epoch: 2 2976/10230. Loss: 0.5429580807685852. Time: 0.2031691074371338 s
Train Epoch: 2 3008/10230. Loss: 0.8279885649681091. Time: 0.1425788402557373 s
Train Epoch: 2 3040/10230. Loss: 1.0030344724655151. Time: 0.25617098808288574 s
Train Epoch: 2 3072/10230. Loss: 0.6785821318626404. Time: 0.26647114753723145 s
Train Epoch: 2 3104/10230. Loss: 0.9356706738471985. Time: 0.15042781829833984 s
Train Epoch: 2 3136/10230. Loss: 0.6898588538169861. Time: 0.24344205856323242 s
Train Epoch: 2 3168/10230. Loss: 0.9644951820373535. Time: 0.2025740146636963 s
Train Epoch: 2 3200/10230. Loss: 0.6592488288879395. Time: 0.12656593322753906 s
Train Epoch: 2 3232/10230. Loss: 0.6605405211448669. Time: 0.11776375770568848 s
Train Epoch: 2 3264/10230. Loss: 0.6555333733558655. Time: 0.15332984924316406 s
Train Epoch: 2 3296/10230. Loss: 0.7496498823165894. Time: 0.25951528549194336 s
Train Epoch: 2 3328/10230. Loss: 0.810956597328186. Time: 0.1791989803314209 s
Train Epoch: 2 3360/10230. Loss: 

...

Train Epoch: 246 7808/10230. Loss: nan. Time: 0.2622799873352051 s
Train Epoch: 246 7840/10230. Loss: nan. Time: 0.2319810390472412 s
Train Epoch: 246 7872/10230. Loss: nan. Time: 0.1214139461517334 s
Train Epoch: 246 7904/10230. Loss: nan. Time: 0.14023494720458984 s
Train Epoch: 246 7936/10230. Loss: nan. Time: 0.29060888290405273 s
Train Epoch: 246 7968/10230. Loss: nan. Time: 0.19999074935913086 s
Train Epoch: 246 8000/10230. Loss: nan. Time: 0.19424819946289062 s
Train Epoch: 246 8032/10230. Loss: nan. Time: 0.2274610996246338 s
Train Epoch: 246 8064/10230. Loss: nan. Time: 0.22383999824523926 s
Train Epoch: 246 8096/10230. Loss: nan. Time: 0.16797685623168945 s
Train Epoch: 246 8128/10230. Loss: nan. Time: 0.25213193893432617 s
Train Epoch: 246 8160/10230. Loss: nan. Time: 0.26323914527893066 s
Train Epoch: 246 8192/10230. Loss: nan. Time: 0.3093702793121338 s
Train Epoch: 246 8224/10230. Loss: nan. Time: 0.20556306838989258 s
Train Epoch: 246 8256/10230. Loss: nan. Time: 0.26284

Train Epoch: 247 1440/10230. Loss: nan. Time: 0.2773408889770508 s
Train Epoch: 247 1472/10230. Loss: nan. Time: 0.31253790855407715 s
Train Epoch: 247 1504/10230. Loss: nan. Time: 0.39702820777893066 s
Train Epoch: 247 1536/10230. Loss: nan. Time: 0.22054505348205566 s
Train Epoch: 247 1568/10230. Loss: nan. Time: 0.19815659523010254 s
Train Epoch: 247 1600/10230. Loss: nan. Time: 0.3600890636444092 s
Train Epoch: 247 1632/10230. Loss: nan. Time: 0.22309303283691406 s
Train Epoch: 247 1664/10230. Loss: nan. Time: 0.40917110443115234 s
Train Epoch: 247 1696/10230. Loss: nan. Time: 0.17044472694396973 s
Train Epoch: 247 1728/10230. Loss: nan. Time: 0.1644296646118164 s
Train Epoch: 247 1760/10230. Loss: nan. Time: 0.1521899700164795 s
Train Epoch: 247 1792/10230. Loss: nan. Time: 0.185988187789917 s
Train Epoch: 247 1824/10230. Loss: nan. Time: 0.1255509853363037 s
Train Epoch: 247 1856/10230. Loss: nan. Time: 0.36484384536743164 s
Train Epoch: 247 1888/10230. Loss: nan. Time: 0.1717119

Train Epoch: 247 5344/10230. Loss: nan. Time: 0.23894667625427246 s
Train Epoch: 247 5376/10230. Loss: nan. Time: 0.24303007125854492 s
Train Epoch: 247 5408/10230. Loss: nan. Time: 0.17097687721252441 s
Train Epoch: 247 5440/10230. Loss: nan. Time: 0.3292579650878906 s
Train Epoch: 247 5472/10230. Loss: nan. Time: 0.18129396438598633 s
Train Epoch: 247 5504/10230. Loss: nan. Time: 0.3816556930541992 s
Train Epoch: 247 5536/10230. Loss: nan. Time: 0.1213991641998291 s
Train Epoch: 247 5568/10230. Loss: nan. Time: 0.3494112491607666 s
Train Epoch: 247 5600/10230. Loss: nan. Time: 0.2413620948791504 s
Train Epoch: 247 5632/10230. Loss: nan. Time: 0.19277405738830566 s
Train Epoch: 247 5664/10230. Loss: nan. Time: 0.2172539234161377 s
Train Epoch: 247 5696/10230. Loss: nan. Time: 0.13127899169921875 s
Train Epoch: 247 5728/10230. Loss: nan. Time: 0.2253739833831787 s
Train Epoch: 247 5760/10230. Loss: nan. Time: 0.20546793937683105 s
Train Epoch: 247 5792/10230. Loss: nan. Time: 0.2427489

Train Epoch: 247 9248/10230. Loss: nan. Time: 0.24494385719299316 s
Train Epoch: 247 9280/10230. Loss: nan. Time: 0.2188107967376709 s
Train Epoch: 247 9312/10230. Loss: nan. Time: 0.14494585990905762 s
Train Epoch: 247 9344/10230. Loss: nan. Time: 0.38774991035461426 s
Train Epoch: 247 9376/10230. Loss: nan. Time: 0.17646479606628418 s
Train Epoch: 247 9408/10230. Loss: nan. Time: 0.2571992874145508 s


KeyboardInterrupt: 

In [23]:
report = trainer.test(X_test, y_test, ['neg', 'neutral', 'pos'])
print(report)

              precision    recall  f1-score   support

         neg       0.11      1.00      0.19       345
     neutral       0.00      0.00      0.00      1175
         pos       0.00      0.00      0.00      1677

   micro avg       0.11      0.11      0.11      3197
   macro avg       0.04      0.33      0.06      3197
weighted avg       0.01      0.11      0.02      3197



/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
